In [14]:
import pandas as pd
import seaborn as sb
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB, MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from xgboost import XGBClassifier
from sklearn.feature_selection import SelectKBest, f_regression
from sklearn.preprocessing import StandardScaler

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import sklearn.tree as tree
import matplotlib.pyplot as plt

In [15]:
teams_df = pd.read_csv('data_merged.csv')


In [16]:
#sb.pairplot(teams_df, hue='playoff', vars=teams_df.columns, corner=True)

In [17]:
cor = teams_df.drop(columns=['tmID']).corr()
plt.figure(figsize=(100, 100))
sb.heatmap(cor, annot=True, cmap=plt.cm.Reds)

<Axes: >

In [19]:
cor.drop(columns=["o_fgm","o_fga","o_ftm","o_fta","o_3pm","o_3pa","o_oreb","o_dreb","o_reb","o_asts","o_pf","o_stl","o_to","o_blk","o_pts","d_fgm","d_fga","d_ftm","d_fta","d_3pm","d_3pa","d_oreb","d_dreb","d_reb","d_asts","d_pf","d_stl","d_to","d_blk","d_pts"], inplace=True)

plt.figure(figsize=(100, 100))
sb.heatmap(cor, annot=True, cmap=plt.cm.Reds)

<Axes: >

## Feature selection with Kbest

In [ ]:
X=teams_df.drop(['playoff', 'tmID'], axis=1)
Y=teams_df['playoff']
fs = SelectKBest(score_func=f_regression, k=20)
# apply feature selection
X_selected = fs.fit_transform(X, Y)
print(X_selected.shape)

(142, 20)


In [ ]:
# Get the selected feature indices using get_support()
selected_feature_indices = fs.get_support()

# Get the column names of the selected features
selected_column_names = X.columns[selected_feature_indices]

# Print the selected column names
print(selected_column_names)

Index(['total_wins', 'total_losses', 'PostGS', 'PostMinutes', 'PostPoints',
       'PostoRebounds', 'PostdRebounds', 'PostRebounds', 'PostAssists',
       'PostSteals', 'PostBlocks', 'PostTurnovers', 'PostPF',
       'PostfgAttempted', 'PostfgMade', 'PostftAttempted', 'PostftMade',
       'award_count', 'W', 'L'],
      dtype='object')


In [ ]:
selected_column_names=selected_column_names.append( pd.Index(['playoff', 'year']) )
final_data = teams_df[selected_column_names]
final_data.to_csv('final_data1.csv', index=False)


## Foward Feature selection

In [ ]:
from mlxtend.feature_selection import SequentialFeatureSelector as SFS

ds=DecisionTreeClassifier()
ffs = SFS(ds, k_features='best', forward=True, n_jobs=-1)
ffs.fit(X, Y)
features = list(ffs.k_feature_names_)
print(features)

['o_to', 'd_ftm', 'd_stl', 'GP_x', 'total_first_round_won', 'total_first_round_lost', 'total_finals_won', 'total_finals_lost', 'PostMinutes', 'PostRebounds', 'PostSteals', 'PostBlocks', 'PostTurnovers', 'PostftMade', 'PostthreeAttempted', 'award_count', 'post_losses', 'W', 'L']


In [ ]:
features += ['playoff', 'year']
final_data = teams_df[features]
final_data.to_csv('final_data2.csv', index=False)